# Laden der Rohdaten

In [25]:
import pickle

# Laden der 'kirp' Liste aus der Pickle-Datei
with open('rick.pickle', 'rb') as f:
    data_frame = pickle.load(f)

# PCA Klasse zu Reduktion der Dimensionen

In [26]:
from torch.utils.data import Dataset
import torch
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from typing import List, Tuple


class GenomeDataset(Dataset):
    """
    Eine benutzerdefinierte Dataset-Klasse, die für die Handhabung von Genomdaten konzipiert ist.
    Diese Klasse wendet eine Principal Component Analysis (PCA) auf die Frequenzen der Genome an
    und teilt den Datensatz in Trainings- und Validierungsteile auf.

    Attributes:
        dataframe (pd.DataFrame): Ein Pandas DataFrame, der die initialen Daten enthält.
        train_df (pd.DataFrame): Ein DataFrame, der den Trainingsdatensatz nach der Anwendung von PCA und der Aufteilung enthält.
        val_df (pd.DataFrame): Ein DataFrame, der den Validierungsdatensatz nach der Anwendung von PCA und der Aufteilung enthält.

    Methods:
        __init__(self, dataframe, n_pca_components=1034, train_size=0.8, split_random_state=42):
            Konstruktor für die GenomeDataset Klasse.
        _do_PCA(self, frequencies, n_components=1034):
            Wendet PCA auf die gegebenen Frequenzen an.
        _split_dataset(self, train_size=0.8, random_state=42):
            Teilt den DataFrame in Trainings- und Validierungsdatensätze auf.
        __getitem__(self, index):
            Gibt ein Tupel aus transformierten Frequenzen und dem zugehörigen Krebstyp für einen gegebenen Index zurück.
        __len__(self):
            Gibt die Gesamtlänge der kombinierten Trainings- und Validierungsdatensätze zurück.
    """

    def __init__(self, dataframe: pd.DataFrame, n_pca_components: int = 1034, train_size: float = 0.8, split_random_state: int = 42):
        """
        Konstruktor für die GenomeDataset Klasse.

        Parameters:
            dataframe (pd.DataFrame): Der DataFrame, der die Genome Frequenzen und Krebsarten enthält.
            n_pca_components (int): Die Anzahl der PCA-Komponenten, auf die reduziert werden soll. Standardwert ist 1034.
            train_size (float): Der Anteil der Daten, der als Trainingsdaten verwendet werden soll. Standardwert ist 0.8.
            split_random_state (int): Der Zufalls-Saatwert, der für die Aufteilung des Datensatzes verwendet wird. Standardwert ist 42.
        """
        self.dataframe = dataframe

        # Umwandlung der Krebsarten in numerische Werte
        self.label_encoder = LabelEncoder()
        self.dataframe['encoded_cancer_type'] = self.label_encoder.fit_transform(dataframe['cancer_type'])

        # Anwenden der PCA auf die Frequenzen
        self.dataframe['pca_frequencies'] = self._do_PCA(self.dataframe['genome_frequencies'].tolist(), n_pca_components)

        # Teilen des DataFrame in Trainings- und Validierungsdatensatz
        self._split_dataset(train_size=train_size, random_state=split_random_state)

    def transform_datapoint(self, datapoint: List[float]) -> List[float]:
        """
        Transformiert einen einzelnen Datenpunkt durch Standardisierung und Anwendung der PCA.

        Diese Methode nimmt einen rohen Datenpunkt (eine Liste von Frequenzen), standardisiert ihn mit dem 
        zuvor angepassten Scaler und wendet dann die PCA-Transformation an, um ihn in den reduzierten 
        Feature-Raum zu überführen, der für das Training des Modells verwendet wurde.

        Parameters:
            datapoint (List[float]): Ein roher Datenpunkt, bestehend aus einer Liste von Frequenzen.

        Returns:
            List[float]: Der transformierte Datenpunkt, nach Anwendung der Standardisierung und der PCA.
        """
        # Standardisierung des Datenpunkts
        scaled_data_point = self.scaler.transform([datapoint])

        # PCA-Transformation des standardisierten Datenpunkts
        pca_transformed_point = self.pca.transform(scaled_data_point)

        return pca_transformed_point.tolist()

    def _do_PCA(self, frequencies: List[List[float]], n_components: int = 1034) -> List[List[float]]:
        """
        Wendet PCA auf die gegebenen Frequenzen an.

        Parameters:
            frequencies (List[List[float]]): Die Liste der Frequenzen, auf die die PCA angewendet werden soll.
            n_components (int): Die Anzahl der Komponenten für die PCA. Standardwert ist 1034.

        Returns:
            List[List[float]]: Eine Liste von Listen, die die transformierten Frequenzen nach der PCA darstellt.
        """

        # Standardisieren der Frequenzen
        self.scaler = StandardScaler()
        scaled_frequencies = self.scaler.fit_transform(frequencies)

        # PCA-Instanz erstellen und auf die gewünschte Anzahl von Komponenten reduzieren
        self.pca = PCA(n_components=n_components)

        # PCA auf die Frequenzen anwenden
        pca_result = self.pca.fit_transform(scaled_frequencies)

        return pca_result.tolist()

    def _split_dataset(self, train_size: float = 0.8, random_state: int = 42):
        """
        Teilt den DataFrame in Trainings- und Validierungsdatensätze auf.

        Parameters:
            train_size (float): Der Anteil der Daten, der als Trainingsdaten verwendet werden soll.
            random_state (int): Der Zufalls-Saatwert, der für die Aufteilung des Datensatzes verwendet wird.
        """

        class SplittedDataset(Dataset):
            def __init__(self, dataframe):
                self.dataframe = dataframe

                # Umwandlung der Genome Frequenzen in Tensoren
                self.genome_frequencies = torch.tensor(dataframe['pca_frequencies'].tolist(), dtype=torch.float32)

                # Umwandlung der Krebsarten in numerische Werte
                self.label_encoder = LabelEncoder()
                self.cancer_types = torch.tensor(dataframe['encoded_cancer_type'].tolist(), dtype=torch.long)

            def __getitem__(self, index):
                # Rückgabe eines Tupels aus Genome Frequenzen und dem entsprechenden Krebstyp
                return self.genome_frequencies[index], self.cancer_types[index]

            def __len__(self):
                return len(self.dataframe)

        # Teilen des DataFrame in Trainings- und Validierungsdatensatz
        train_df, val_df = train_test_split(self.dataframe, train_size=train_size, random_state=random_state)
        self.train_df = SplittedDataset(train_df)
        self.val_df = SplittedDataset(val_df)


    def __getitem__(self, index: int) -> Tuple[torch.Tensor, int]:
        """
        Gibt ein Tupel aus transformierten Frequenzen und dem entsprechenden Krebstyp für einen gegebenen Index zurück.

        Parameters:
            index (int): Der Index des zu abrufenden Datenelements.

        Returns:
            Tuple[torch.Tensor, int]: Ein Tupel, bestehend aus einem Tensor der transformierten Frequenzen und dem zugehörigen Krebstyp.
        """

        print(self.train_df.shape)
        print(self.val_df.shape)
        
        if index < len(self.train_df):
            row = self.train_df.iloc[index]
        else:
            row = self.val_df.iloc[len(self.train_df) - index]

        pca_frequencies_tensor = torch.tensor(row['pca_frequencies'], dtype=torch.float32)
        cancer_type = row['encoded_cancer_type']

        return pca_frequencies_tensor, cancer_type

    def __len__(self) -> int:
        """
        Gibt die Gesamtlänge der kombinierten Trainings- und Validierungsdatensätze zurück.

        Returns:
            int: Die Länge der kombinierten Datensätze.
        """
        
        return len(self.train_df) + len(self.val_df)


# Definition des neuronalen Netzes

In [27]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F

class CancerClassifierNN(nn.Module):
    """
    Eine benutzerdefinierte neuronale Netzwerkklassifikator-Klasse für die Krebsklassifikation.

    Diese Klasse definiert ein mehrschichtiges Perzeptron (MLP), das für die Klassifizierung von Krebsarten
    anhand genetischer Frequenzdaten verwendet wird.

    Attributes:
        fc1 (nn.Linear): Die erste lineare Schicht des Netzwerks.
        fc2 (nn.Linear): Die zweite lineare Schicht des Netzwerks.
        fc3 (nn.Linear): Die dritte lineare Schicht des Netzwerks.
        fc4 (nn.Linear): Die Ausgabeschicht des Netzwerks.
        dropout (nn.Dropout): Ein Dropout-Layer zur Vermeidung von Overfitting.

    Methods:
        __init__(self, input_size: int, num_classes: int):
            Konstruktor für die CancerClassifierNN Klasse.
        forward(self, x: torch.Tensor) -> torch.Tensor:
            Definiert den Vorwärtsdurchlauf des Netzwerks.
    """

    def __init__(self, input_size: int, num_classes: int):
        """
        Konstruktor für die CancerClassifierNN Klasse.

        Parameters:
            input_size (int): Die Größe des Input-Features.
            num_classes (int): Die Anzahl der Zielklassen.
        """
        super(CancerClassifierNN, self).__init__()
        # Definieren der Schichten
        self.fc1 = nn.Linear(input_size, 1024)  # Eingabeschicht
        self.fc2 = nn.Linear(1024, 512)        # Versteckte Schicht
        self.fc3 = nn.Linear(512, 256)         # Weitere versteckte Schicht
        self.fc4 = nn.Linear(256, num_classes) # Ausgabeschicht
        self.dropout = nn.Dropout(p=0.5)       # Dropout

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        """
        Definiert den Vorwärtsdurchlauf des Netzwerks.

        Parameters:
            x (torch.Tensor): Der Input-Tensor für das Netzwerk.

        Returns:
            torch.Tensor: Der Output-Tensor nach dem Durchlauf durch das Netzwerk.
        """
        x = F.relu(self.fc1(x))
        x = self.dropout(x)
        x = F.relu(self.fc2(x))
        x = self.dropout(x)
        x = F.relu(self.fc3(x))
        x = torch.sigmoid(self.fc4(x))  # Oder F.log_softmax(x, dim=1) für Mehrklassenklassifikation
        return x

In [28]:
from torch.utils.data import DataLoader

# Erstellen der Dataframe Klasse
genome_dataset = GenomeDataset(data_frame)
train_dataset = genome_dataset.train_df
valid_dataset = genome_dataset.val_df

# Annahme: input_size ist die Länge Ihrer Genome-Frequenzen und num_classes ist die Anzahl der Krebsarten
model = CancerClassifierNN(input_size=1034, num_classes=3)

# Daten-Loader
train_loader = DataLoader(dataset=train_dataset, batch_size=64, shuffle=True)
valid_loader = DataLoader(dataset=valid_dataset, batch_size=64, shuffle=False)

In [29]:
import torch.optim as optim

# Verlustfunktion
criterion = nn.CrossEntropyLoss()

# Optimierer
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Anzahl der Epochen
num_epochs = 10


In [30]:
# Listen, um Verluste zu speichern
train_losses = []
valid_losses = []

for epoch in range(num_epochs):
    model.train()
    train_loss = 0.0
    for i, (inputs, labels) in enumerate(train_loader):
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        train_loss += loss.item()

    # Durchschnittlicher Trainingsverlust
    train_loss /= len(train_loader)
    train_losses.append(train_loss)

    # Validierungsverlust
    model.eval()
    valid_loss = 0.0
    with torch.no_grad():
        for inputs, labels in valid_loader:
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            valid_loss += loss.item()

    # Durchschnittlicher Validierungsverlust
    valid_loss /= len(valid_loader)
    valid_losses.append(valid_loss)

    print(f'Epoch [{epoch+1}/{num_epochs}], Trainingsverlust: {train_loss:.4f}, Validierungsverlust: {valid_loss:.4f}')

Epoch [1/10], Trainingsverlust: 0.8623, Validierungsverlust: 0.7387
Epoch [2/10], Trainingsverlust: 0.7593, Validierungsverlust: 0.7306
Epoch [3/10], Trainingsverlust: 0.7496, Validierungsverlust: 0.7388
Epoch [4/10], Trainingsverlust: 0.7466, Validierungsverlust: 0.7342
Epoch [5/10], Trainingsverlust: 0.7456, Validierungsverlust: 0.7340
Epoch [6/10], Trainingsverlust: 0.7454, Validierungsverlust: 0.7265
Epoch [7/10], Trainingsverlust: 0.7448, Validierungsverlust: 0.7252
Epoch [8/10], Trainingsverlust: 0.7469, Validierungsverlust: 0.7239
Epoch [9/10], Trainingsverlust: 0.7453, Validierungsverlust: 0.7242
Epoch [10/10], Trainingsverlust: 0.7449, Validierungsverlust: 0.7252
